In [ ]:
%%capture
!git clone https://github.com/AI4Bharat/IndicTrans2.git

In [ ]:
%%capture
%cd /content/IndicTrans2/huggingface_interface

In [ ]:
%%capture
!python3 -m pip install nltk sacremoses pandas regex mock transformers>=4.33.2 mosestokenizer
!python3 -c "import nltk; nltk.download('punkt')"
!python3 -m pip install bitsandbytes scipy accelerate datasets
!python3 -m pip install sentencepiece

!git clone https://github.com/VarunGumma/IndicTransToolkit
%cd IndicTransToolkit

!pip install --editable . --use-pep517 # required for pip >= 25.0

# !git clone https://github.com/VarunGumma/IndicTransToolkit.git
# %cd IndicTransToolkit
# !python3 -m pip install --editable ./
# %cd ..

In [ ]:
!pip uninstall IndicTransToolkit -y
!pip install git+https://github.com/VarunGumma/IndicTransToolkit.git

Found existing installation: IndicTransToolkit 1.0.3
Uninstalling IndicTransToolkit-1.0.3:
  Successfully uninstalled IndicTransToolkit-1.0.3
  Cloning https://github.com/VarunGumma/IndicTransToolkit.git to /tmp/pip-req-build-1i_nw24e
  Running command git clone --filter=blob:none --quiet https://github.com/VarunGumma/IndicTransToolkit.git /tmp/pip-req-build-1i_nw24e
  Resolved https://github.com/VarunGumma/IndicTransToolkit.git to commit 9ca9208435d2d24514b592286e89eb115483d2fb
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/VarunGumma/indic_nlp_library.git to /tmp/pip-install-p0swvbhs/indic-nlp-library-it2_68e5906dfade49bebfb14e5b31208834
  Running command git clone --filter=blob:none --quiet https://github.com/VarunGumma/indic_nlp_library.git /tmp/pip-install-p0swvbhs/indic-nlp-library-it2_68e5906dfade49bebfb14e5b31208834
  Resolved https://github.com/VarunGumma/indic_

In [ ]:
!pip install git+https://github.com/VarunGumma/IndicTransToolkit.git

  Cloning https://github.com/VarunGumma/IndicTransToolkit.git to /tmp/pip-req-build-g2kc7bzw
  Running command git clone --filter=blob:none --quiet https://github.com/VarunGumma/IndicTransToolkit.git /tmp/pip-req-build-g2kc7bzw
  Resolved https://github.com/VarunGumma/IndicTransToolkit.git to commit 9ca9208435d2d24514b592286e89eb115483d2fb
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/VarunGumma/indic_nlp_library.git to /tmp/pip-install-gd_nystw/indic-nlp-library-it2_5a11821970f44826b0ec349cb85693ac
  Running command git clone --filter=blob:none --quiet https://github.com/VarunGumma/indic_nlp_library.git /tmp/pip-install-gd_nystw/indic-nlp-library-it2_5a11821970f44826b0ec349cb85693ac
  Resolved https://github.com/VarunGumma/indic_nlp_library.git to commit 342a7e95735e88949528bdca371518cb0ba5bb5d
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
import torch
from transformers import AutoModelForSeq2SeqLM, BitsAndBytesConfig, AutoTokenizer
from IndicTransToolkit import IndicProcessor

BATCH_SIZE = 4
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
quantization = None

In [ ]:
def initialize_model_and_tokenizer(ckpt_dir, quantization):
    if quantization == "4-bit":
        qconfig = BitsAndBytesConfig(
            load_in_4bit=True,
            bnb_4bit_use_double_quant=True,
            bnb_4bit_compute_dtype=torch.bfloat16,
        )
    elif quantization == "8-bit":
        qconfig = BitsAndBytesConfig(
            load_in_8bit=True,
            bnb_8bit_use_double_quant=True,
            bnb_8bit_compute_dtype=torch.bfloat16,
        )
    else:
        qconfig = None

    tokenizer = AutoTokenizer.from_pretrained(ckpt_dir, trust_remote_code=True)
    model = AutoModelForSeq2SeqLM.from_pretrained(
        ckpt_dir,
        trust_remote_code=True,
        low_cpu_mem_usage=True,
        quantization_config=qconfig,
    )

    if qconfig == None:
        model = model.to(DEVICE)
        if DEVICE == "cuda":
            model.half()

    model.eval()

    return tokenizer, model


def batch_translate(input_sentences, src_lang, tgt_lang, model, tokenizer, ip):
    translations = []
    for i in range(0, len(input_sentences), BATCH_SIZE):
        batch = input_sentences[i : i + BATCH_SIZE]

        # Preprocess the batch and extract entity mappings
        batch = ip.preprocess_batch(batch, src_lang=src_lang, tgt_lang=tgt_lang)

        # Tokenize the batch and generate input encodings
        inputs = tokenizer(
            batch,
            truncation=True,
            padding="longest",
            return_tensors="pt",
            return_attention_mask=True,
        ).to(DEVICE)

        # Generate translations using the model
        with torch.no_grad():
            generated_tokens = model.generate(
                **inputs,
                use_cache=True,
                min_length=0,
                max_length=256,
                num_beams=5,
                num_return_sequences=1,
            )

        # Decode the generated tokens into text

        with tokenizer.as_target_tokenizer():
            generated_tokens = tokenizer.batch_decode(
                generated_tokens.detach().cpu().tolist(),
                skip_special_tokens=True,
                clean_up_tokenization_spaces=True,
            )

        # Postprocess the translations, including entity replacement
        translations += ip.postprocess_batch(generated_tokens, lang=tgt_lang)

        del inputs
        torch.cuda.empty_cache()

    return translations

In [ ]:
pip install datasets sacrebleu

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 31.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.9/183.9 kB 17.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 15.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 19.0 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2025.3.2 requires fsspec==2025.3.2, but you have fsspec 2024.12.0 which is incompatible.


In [ ]:
pip install datasets sacrebleu
!pip install sacrebleu unbabel-comet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.8/51.8 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.5/55.5 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 4.8 MB/s eta 0:00:00
ERROR: Operation cancelled by user


In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) n
Token is valid (permission: read).
The token `DivyaKapse` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
The current active token is: `DivyaKapse`


In [ ]:
from datasets import load_dataset
from sacrebleu import corpus_bleu

# Load dataset
dataset = load_dataset("ai4bharat/IN22-Gen", split="test")

# Extract English and Hindi sentence pairs
src_sentences = dataset["eng_Latn"]  # English Sentences
ref_sentences = dataset["hin_Deva"]  # Reference Hindi Translations

README.md:   0%|          | 0.00/7.71k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/4.34M [00:00<?, ?B/s]

Generating test split:   0%|          | 0/1024 [00:00<?, ? examples/s]

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "hin_Deva"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(



eng_Latn - hin_Deva
eng_Latn: An appearance is a bunch of attributes related to the service person, like their shoes, clothes, tie, jewellery, hairstyle, make-up, watch, cosmetics, perfume, etc.
hin_Deva: उपस्थिति सेवा करने वाले व्यक्ति से संबंधित विशेषताओं का एक समूह है, जैसे कि उनके जूते, कपड़े, टाई, आभूषण, केश शैली, मेकअप, घड़ी, सौंदर्य प्रसाधन, इत्र आदि। 
eng_Latn: Ajanta, located in the Aurangabad District of Maharashtra has twenty-nine caitya and vihara caves decorated with sculptures and paintings from the first century B.C.E. to the fifth century C.E.
hin_Deva: महाराष्ट्र के औरंगाबाद जिले में स्थित अजंता में उनतीस चैत्य और विहार गुफाएं हैं जो पहली शताब्दी ईसा पूर्व से लेकर पांचवीं शताब्दी ईसा पूर्व तक की मूर्तियों और चित्रों से सजी हुई हैं। 
eng_Latn: Body colour gets merged with the outer line, creating the effect of volume.
hin_Deva: शरीर का रंग बाहरी रेखा के साथ मिल जाता है, जिससे आयतन का प्रभाव पैदा होता है। 
eng_Latn: Ashoka started making extensive use of stone for sculp

In [ ]:
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 32.79


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 57.96


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.migration.utils:Lightning automatically upgraded your loaded checkpoint from v1.8.3.post1 to v2.5.1. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint ../root/.cache/huggingface/hub/models--Unbabel--wmt22-comet-da/snapshots/2760a223ac957f30acfb18c8aa649b01cf1d75f2/checkpoints/model.ckpt`
/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:p

COMET Score: 0.80


In [ ]:
from datasets import load_dataset
from sacrebleu import corpus_bleu

# Load dataset
dataset = load_dataset("ai4bharat/IN22-Gen", split="test")

# Extract English and Hindi sentence pairs
src_sentences = dataset["eng_Latn"]  # English Sentences
ref_guj_sentences = dataset["guj_Gujr"]  # Reference Hindi Translations

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/7.71k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/4.34M [00:00<?, ?B/s]

Generating test split:   0%|          | 0/1024 [00:00<?, ? examples/s]

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "guj_Gujr"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model


eng_Latn - guj_Gujr
eng_Latn: An appearance is a bunch of attributes related to the service person, like their shoes, clothes, tie, jewellery, hairstyle, make-up, watch, cosmetics, perfume, etc.
guj_Gujr: દેખાવ એ સેવા આપનાર વ્યક્તિ સાથે સંબંધિત લક્ષણોનો સમૂહ છે, જેમ કે તેમના પગરખાં, કપડાં, ટાઈ, ઘરેણાં, હેરસ્ટાઇલ, મેકઅપ, ઘડિયાળ, સૌંદર્ય પ્રસાધનો, અત્તર વગેરે. 
eng_Latn: Ajanta, located in the Aurangabad District of Maharashtra has twenty-nine caitya and vihara caves decorated with sculptures and paintings from the first century B.C.E. to the fifth century C.E.
guj_Gujr: મહારાષ્ટ્રના ઔરંગાબાદ જિલ્લામાં સ્થિત અજંતામાં 29 ચૈત્ય અને વિહાર ગુફાઓ છે, જે ઇ. સ. પૂર્વે પ્રથમ સદીથી ઇ. સ. પૂર્વે પાંચમી સદી સુધીના શિલ્પો અને ચિત્રોથી સુશોભિત છે. 
eng_Latn: Body colour gets merged with the outer line, creating the effect of volume.
guj_Gujr: શરીરનો રંગ બાહ્ય રેખા સાથે ભળી જાય છે, જે કદની અસર બનાવે છે. 
eng_Latn: Ashoka started making extensive use of stone for sculptures and great monuments, wherea

In [ ]:
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_guj_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 24.58


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_guj_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 56.32


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_guj_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

model.ckpt:   0%|          | 0.00/2.32G [00:00<?, ?B/s]

LICENSE:   0%|          | 0.00/9.69k [00:00<?, ?B/s]

hparams.yaml:   0%|          | 0.00/567 [00:00<?, ?B/s]

.gitattributes:   0%|          | 0.00/1.48k [00:00<?, ?B/s]

...

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/616 [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting DataLoader 0: 100%|██████████| 128/128 [00:42<00:00,  3.02it/s]


COMET Score: 0.88


In [ ]:
!pip install sacrebleu unbabel-comet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.5/55.5 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.4/96.4 kB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.4/101.4 kB 9.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.3/18.3 MB 62.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.6/294.6 kB 24.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.0/823.0 kB 48.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 529.7/529.7 kB 34.3 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.4
    Uninstalling protobuf-5.29.4:
      Successfully uninstalled protobuf-5.29.4
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not current

In [ ]:
from datasets import load_dataset

# Load English (Latin script) devtest split
dataset_eng = load_dataset("openlanguagedata/flores_plus", "eng_Latn", split="devtest")

# Load Hindi (Devanagari script) devtest split
dataset_hin = load_dataset("openlanguagedata/flores_plus", "hin_Deva", split="devtest")

# Set source and reference sentences
src_sentences = dataset_eng["text"]  # English sentences
ref_sentences = dataset_hin["text"]  # Hindi sentences

# Print first 5 sentence pairs as a sanity check
for i in range(5):
    print(f"{i+1}. English: {src_sentences[i]}")
    print(f"   Hindi:   {ref_sentences[i]}")
    print()


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/72.2k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/219 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/213 [00:00<?, ?it/s]

eng_Latn.parquet:   0%|          | 0.00/112k [00:00<?, ?B/s]

...

hin_Deva.parquet:   0%|          | 0.00/161k [00:00<?, ?B/s]

hin_Deva.parquet:   0%|          | 0.00/168k [00:00<?, ?B/s]

Generating dev split:   0%|          | 0/997 [00:00<?, ? examples/s]

Generating devtest split:   0%|          | 0/1012 [00:00<?, ? examples/s]

1. English: "We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.
   Hindi:   उन्होंने कहा “कि अब हमारे पास 4 महीने उम्र वाले चूहे हैं जिन्हें मधुमेह नहीं है जो मधुमेह के रोगी थे। ”

2. English: Dr. Ehud Ur, professor of medicine at Dalhousie University in Halifax, Nova Scotia and chair of the clinical and scientific division of the Canadian Diabetes Association cautioned that the research is still in its early days.
   Hindi:   डॉ. एहुड उर, नोवा स्कोटिया के हैलिफ़ैक्स में डलहौज़ी विश्वविद्यालय में चिकित्सा के प्रोफ़ेसर और कनाडाई डायबिटीज़ एसोसिएशन के नैदानिक ​​और वैज्ञानिक विभाग के अध्यक्ष ने आगाह किया कि शोध अभी भी अपने शुरुआती दिनों में है.

3. English: Like some other experts, he is skeptical about whether diabetes can be cured, noting that these findings have no relevance to people who already have Type 1 diabetes.
   Hindi:   कुछ अन्य विशेषज्ञों की तरह, उन्हें इस बात पर संदेह है कि क्या मधुमेह को ठीक किया जा सकता है, यह देखते हुए कि इन निष्कर्षो

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "hin_Deva"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model

tokenizer_config.json:   0%|          | 0.00/1.10k [00:00<?, ?B/s]

tokenization_indictrans.py:   0%|          | 0.00/8.13k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/ai4bharat/indictrans2-en-indic-1B:
- tokenization_indictrans.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


dict.SRC.json:   0%|          | 0.00/645k [00:00<?, ?B/s]

dict.TGT.json:   0%|          | 0.00/3.39M [00:00<?, ?B/s]

...

A new version of the following files was downloaded from https://huggingface.co/ai4bharat/indictrans2-en-indic-1B:
- modeling_indictrans.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


model.safetensors:   0%|          | 0.00/4.46G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/163 [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(



eng_Latn - hin_Deva
eng_Latn: "We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.
hin_Deva: उन्होंने कहा, "अब हमारे पास 4 महीने के चूहे हैं जो गैर-मधुमेह वाले हैं जो पहले मधुमेह के मरीज हुआ करते थे।" 
eng_Latn: Dr. Ehud Ur, professor of medicine at Dalhousie University in Halifax, Nova Scotia and chair of the clinical and scientific division of the Canadian Diabetes Association cautioned that the research is still in its early days.
hin_Deva: डॉ. एहुद उर, हैलिफ़ैक्स, नोवा स्कोटिया में डलहौज़ी विश्वविद्यालय में चिकित्सा के प्रोफेसर और कैनेडियन डायबिटीज़ एसोसिएशन के नैदानिक और वैज्ञानिक विभाग के अध्यक्ष ने आगाह किया कि शोध अभी भी अपने शुरुआती दिनों में है। 
eng_Latn: Like some other experts, he is skeptical about whether diabetes can be cured, noting that these findings have no relevance to people who already have Type 1 diabetes.
hin_Deva: कुछ अन्य विशेषज्ञों की तरह, उन्हें इस बारे में संदेह है कि क्या मधुमेह का इलाज किया जा सकता है, यह देखते हुए कि

In [ ]:
from sacrebleu import corpus_bleu
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 36.54


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 60.84


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

model.ckpt:   0%|          | 0.00/2.32G [00:00<?, ?B/s]

hparams.yaml:   0%|          | 0.00/567 [00:00<?, ?B/s]

.gitattributes:   0%|          | 0.00/1.48k [00:00<?, ?B/s]

LICENSE:   0%|          | 0.00/9.69k [00:00<?, ?B/s]

...

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/616 [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting DataLoader 0: 100%|██████████| 127/127 [00:30<00:00,  4.14it/s]


COMET Score: 0.82


In [ ]:
from datasets import load_dataset

# Load English (Latin script) devtest split
dataset_eng = load_dataset("openlanguagedata/flores_plus", "eng_Latn", split="devtest")

# Load Hindi (Devanagari script) devtest split
dataset_hin = load_dataset("openlanguagedata/flores_plus", "guj_Gujr", split="devtest")

# Set source and reference sentences
src_sentences = dataset_eng["text"]  # English sentences
ref_sentences = dataset_hin["text"]  # Hindi sentences

# Print first 5 sentence pairs as a sanity check
for i in range(5):
    print(f"{i+1}. English: {src_sentences[i]}")
    print(f"   Hindi:   {ref_sentences[i]}")
    print()


Resolving data files:   0%|          | 0/219 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/213 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/219 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/213 [00:00<?, ?it/s]

guj_Gujr.parquet:   0%|          | 0.00/162k [00:00<?, ?B/s]

guj_Gujr.parquet:   0%|          | 0.00/170k [00:00<?, ?B/s]

Generating dev split:   0%|          | 0/997 [00:00<?, ? examples/s]

Generating devtest split:   0%|          | 0/1012 [00:00<?, ? examples/s]

1. English: "We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.
   Hindi:   "તેમણે ઉમેર્યું, ""હવે અમારી પાસે 4 મહિના પહેલા જન્મેલા ઉંદરો છે જેઓ પહેલા ડાયાબિટીસથી પીડાતા હતા પરંતુ હવે તેઓને ડાયાબિટીસ નથી."""

2. English: Dr. Ehud Ur, professor of medicine at Dalhousie University in Halifax, Nova Scotia and chair of the clinical and scientific division of the Canadian Diabetes Association cautioned that the research is still in its early days.
   Hindi:   તબીબી પ્રાધ્યાપક, ડેલહાઉસી યુનિવર્સિટી, હેલીફેક્સ, નોવા સ્કોટિયા અને કેનેડીયન  ડાયાબિટીસ એસોસિએશન ના ક્લિનિકલ અને સાયન્ટિફિક ડિવિઝન ના ચેર, ડો. ઈહુદ ઉર એ ચેતવણી આપી કે સંશોધન હજી પણ તેના પ્રાથમિક તબક્કા માં છે.

3. English: Like some other experts, he is skeptical about whether diabetes can be cured, noting that these findings have no relevance to people who already have Type 1 diabetes.
   Hindi:   કેટલાક અન્ય નિષ્ણાતોની જેમ તેઓ પણ ડાયાબિટીસ મટી શકે કે કેમ એ અંગે શંકા ધરાવે છે, એ ધ્યાનમાં લેતા કે આ

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "guj_Gujr"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(



eng_Latn - guj_Gujr
eng_Latn: "We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.
guj_Gujr: "હવે આપણી પાસે 4 મહિનાના ઉંદર છે જે બિન-ડાયાબિટીક છે જે પહેલાં ડાયાબિટીક હતા", તેમણે ઉમેર્યું. 
eng_Latn: Dr. Ehud Ur, professor of medicine at Dalhousie University in Halifax, Nova Scotia and chair of the clinical and scientific division of the Canadian Diabetes Association cautioned that the research is still in its early days.
guj_Gujr: ડૉ. એહુદ ઉર, હેલિફેક્સ, નોવા સ્કોટીયામાં ડેલહાઉસી યુનિવર્સિટીમાં મેડિસિનના પ્રોફેસર અને કેનેડિયન ડાયાબિટીસ એસોસિએશનના ક્લિનિકલ અને વૈજ્ઞાનિક વિભાગના અધ્યક્ષે ચેતવણી આપી હતી કે સંશોધન હજુ પણ તેના પ્રારંભિક દિવસોમાં છે. 
eng_Latn: Like some other experts, he is skeptical about whether diabetes can be cured, noting that these findings have no relevance to people who already have Type 1 diabetes.
guj_Gujr: કેટલાક અન્ય નિષ્ણાતોની જેમ, તેઓ ડાયાબિટીસને મટાડી શકાય કે કેમ તે અંગે શંકાસ્પદ છે, તેમણે નોંધ્યું હતું કે આ તારણો એવા લોકો

In [ ]:
from sacrebleu import corpus_bleu
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 26.91


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 58.93


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.migration.utils:Lightning automatically upgraded your loaded checkpoint from v1.8.3.post1 to v2.5.1. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint ../root/.cache/huggingface/hub/models--Unbabel--wmt22-comet-da/snapshots/2760a223ac957f30acfb18c8aa649b01cf1d75f2/checkpoints/model.ckpt`
/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:p

COMET Score: 0.89


In [ ]:
!pip install sacrebleu unbabel-comet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.5/55.5 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.0/91.0 kB 9.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.4/101.4 kB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.3/18.3 MB 93.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.6/294.6 kB 31.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.0/823.0 kB 60.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 529.7/529.7 kB 50.3 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.4
    Uninstalling protobuf-5.29.4:
      Successfully uninstalled protobuf-5.29.4
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not curren

In [ ]:
from datasets import load_dataset
from sacrebleu import corpus_bleu

dataset = load_dataset("wmt/wmt14", "hi-en", split="test")

# Extract English and Hindi sentence pairs
src_sentences = [item["en"] for item in dataset["translation"][:1000]]
ref_sentences = [item["hi"] for item in dataset["translation"][:1000]]

# Check a few samples
print(src_sentences[:5])
print(ref_sentences[:5])

# Optional: check number of examples
print(len(src_sentences), len(ref_sentences))


['A black box in your car?', "As America's road planners struggle to find the cash to mend a crumbling highway system, many are beginning to see a solution in a little black box that fits neatly by the dashboard of your car.", "The devices, which track every mile a motorist drives and transmit that information to bureaucrats, are at the center of a controversial attempt in Washington and state planning offices to overhaul the outdated system for funding America's major roads.", 'The usually dull arena of highway planning has suddenly spawned intense debate and colorful alliances.', 'Libertarians have joined environmental groups in lobbying to allow government to use the little boxes to keep track of the miles you drive, and possibly where you drive them - then use the information to draw up a tax bill.']
['आपकी कार में ब्लैक बॉक्स?', 'जबकि अमेरिका के सड़क योजनाकार, ध्वस्त होते हुए हाईवे सिस्टम को सुधारने के लिए धन की कमी से जूझ रहे हैं, वहीं बहुत-से लोग इसका समाधान छोटे से ब्लैक बॉक्स 

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "hin_Deva"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(



eng_Latn - hin_Deva
eng_Latn: A black box in your car?
hin_Deva: आपकी गाड़ी में ब्लैक बॉक्स है? 
eng_Latn: As America's road planners struggle to find the cash to mend a crumbling highway system, many are beginning to see a solution in a little black box that fits neatly by the dashboard of your car.
hin_Deva: जैसे-जैसे अमेरिका के सड़क योजनाकार एक जर्जर राजमार्ग प्रणाली को ठीक करने के लिए नकदी खोजने के लिए संघर्ष कर रहे हैं, कई लोगों को एक छोटे से ब्लैक बॉक्स में एक समाधान दिखाई देने लगा है जो आपकी कार के डैशबोर्ड पर अच्छी तरह से फिट बैठता है। 
eng_Latn: The devices, which track every mile a motorist drives and transmit that information to bureaucrats, are at the center of a controversial attempt in Washington and state planning offices to overhaul the outdated system for funding America's major roads.
hin_Deva: ये उपकरण, जो एक मोटर चालक द्वारा चलाए जाने वाले हर मील को ट्रैक करते हैं और नौकरशाहों को उस जानकारी को प्रसारित करते हैं, वाशिंगटन और राज्य योजना कार्यालयों में अमेरिका की प्र

In [ ]:
from sacrebleu import corpus_bleu
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 25.83


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 53.74


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

README.md:   0%|          | 0.00/3.40k [00:00<?, ?B/s]

.gitattributes:   0%|          | 0.00/1.48k [00:00<?, ?B/s]

hparams.yaml:   0%|          | 0.00/567 [00:00<?, ?B/s]

LICENSE:   0%|          | 0.00/9.69k [00:00<?, ?B/s]

...

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/616 [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting DataLoader 0: 100%|██████████| 125/125 [00:24<00:00,  5.07it/s]


COMET Score: 0.80


In [ ]:
from datasets import load_dataset
from sacrebleu import corpus_bleu

dataset = load_dataset("wmt/wmt19", "gu-en", split="validation")

# Extract English and Hindi sentence pairs
src_sentences = [item["en"] for item in dataset["translation"][:1000]]
ref_sentences = [item["gu"] for item in dataset["translation"][:1000]]

# Check a few samples
print(src_sentences[:5])
print(ref_sentences[:5])

# Optional: check number of examples
print(len(src_sentences), len(ref_sentences))



train-00000-of-00001.parquet:   0%|          | 0.00/361k [00:00<?, ?B/s]

validation-00000-of-00001.parquet:   0%|          | 0.00/370k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/11670 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1998 [00:00<?, ? examples/s]

['Thousands in Central Park panic after barrier collapse', 'The collapse of a police barrier sent thousands of people fleeing in a panic in Central Park, afraid of possible gunshots at a politically-charged show.', "Big-name personalities from Democratic New York Gov. Andrew Cuomo and Republican Sen. Jeff Flake to Janet Jackson and John Legend urged spectators to get involved in the nation's troubled politics.", 'Authorities quickly assured the crowd they were safe after the barrier fell Saturday evening.', 'Burning social justice issues dominated the event that started on a sunny afternoon.']
['બેરિયર ભાંગી ગયા પછી સેન્ટ્રલ પાર્કમાં હજારો ગભરાટમાં', 'એક રાજકીય કાર્યક્રમમાં પોલીસ બેરીયરના ભંગાણને કારણે સેન્ટ્રલ પાર્કમાં નાસભાગ કરતાં હજારો લોકો સંભવિત બંદૂકની ગોળીઓના ભયથી મુશ્કેલીમાં મુકાયા.', 'ડેમોક્રેટિક ન્યૂયોર્ક સરકારની મોટી નામી હસ્તીઓ એન્ડ્ર્યુ કુમો અને જેનેટ જેક્સનના રિપબ્લિકન સેન જેફ ફ્લેક અને જ્હોન લેજેન્ડએ પ્રેક્ષકોને રાષ્ટ્રની મુશ્કેલીમાં રહેલા રાજકારણમાં સામેલ થવા વિનંતી કરી

In [ ]:
en_indic_ckpt_dir = "ai4bharat/indictrans2-en-indic-1B"  # ai4bharat/indictrans2-en-indic-dist-200M
en_indic_tokenizer, en_indic_model = initialize_model_and_tokenizer(en_indic_ckpt_dir, quantization)

ip = IndicProcessor(inference=True)

src_lang, tgt_lang = "eng_Latn", "guj_Gujr"
hi_translations = batch_translate(src_sentences, src_lang, tgt_lang, en_indic_model, en_indic_tokenizer, ip)

print(f"\n{src_lang} - {tgt_lang}")
for input_sentence, translation in zip(src_sentences, hi_translations):
    print(f"{src_lang}: {input_sentence}")
    print(f"{tgt_lang}: {translation}")

# flush the models to free the GPU memory
del en_indic_tokenizer, en_indic_model


eng_Latn - guj_Gujr
eng_Latn: Thousands in Central Park panic after barrier collapse
guj_Gujr: સેન્ટ્રલ પાર્કમાં બેરિયર તૂટી પડતાં હજારો લોકો ગભરાઈ ગયા 
eng_Latn: The collapse of a police barrier sent thousands of people fleeing in a panic in Central Park, afraid of possible gunshots at a politically-charged show.
guj_Gujr: પોલીસ બેરિયર તૂટી પડવાથી સેન્ટ્રલ પાર્કમાં હજારો લોકો ગભરાટમાં ભાગી ગયા હતા, રાજકીય રીતે ચાર્જ કરેલા શોમાં સંભવિત ગોળીબારના ડરથી. 
eng_Latn: Big-name personalities from Democratic New York Gov. Andrew Cuomo and Republican Sen. Jeff Flake to Janet Jackson and John Legend urged spectators to get involved in the nation's troubled politics.
guj_Gujr: ડેમોક્રેટિક ન્યૂયોર્કના ગવર્નર એન્ડ્રુ કુઓમો અને રિપબ્લિકન સેન જેફ ફ્લેકથી લઈને જેનેટ જેક્સન અને જ્હોન લિજેન્ડ સુધીની મોટી હસ્તીઓએ દર્શકોને દેશના અશાંત રાજકારણમાં સામેલ થવા વિનંતી કરી હતી. 
eng_Latn: Authorities quickly assured the crowd they were safe after the barrier fell Saturday evening.
guj_Gujr: શનિવારે સાંજે અવરોધ 

In [ ]:
from sacrebleu import corpus_bleu
# Compute BLEU Score
bleu = corpus_bleu(hi_translations, [ref_sentences])
print(f"BLEU Score: {bleu.score:.2f}")

BLEU Score: 20.07


In [ ]:
from sacrebleu.metrics import CHRF

# Initialize CHRF metric
chrf = CHRF()

# Compute chrF score
chrf_score = chrf.corpus_score(hi_translations, [ref_sentences])

# Print chrF score
print(f"chrF Score: {chrf_score.score:.2f}")


chrF Score: 55.96


In [ ]:
from comet import download_model, load_from_checkpoint

# Download COMET model
comet_model_path = download_model("Unbabel/wmt22-comet-da")
comet_model = load_from_checkpoint(comet_model_path)

# Prepare data for COMET
comet_data = [
    {"src": src, "mt": mt, "ref": ref}
    for src, mt, ref in zip(src_sentences, hi_translations, ref_sentences)
]

# Compute COMET scores
comet_score = comet_model.predict(comet_data, batch_size=8)

# Print COMET score
print(f"COMET Score: {comet_score['system_score']:.2f}")


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.migration.utils:Lightning automatically upgraded your loaded checkpoint from v1.8.3.post1 to v2.5.1. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint ../../../root/.cache/huggingface/hub/models--Unbabel--wmt22-comet-da/snapshots/2760a223ac957f30acfb18c8aa649b01cf1d75f2/checkpoints/model.ckpt`
/usr/local/lib/python3.11/dist-packages/pytorch_lightning/core/saving.py:195: Found keys that are not in the model state dict but in the checkpoint: ['encoder.model.embeddings.position_ids']
INFO:pytorch_lightning.utilities.rank_zero:You are using the plain ModelCheckpoint callback. Consider using LitModelCheckpoint which with seamless uploading to Model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


COMET Score: 0.90
